# Ingest streaming data into S3 using Kinesis Firehose

When interacting with AWS from a Jupyter notebook or python code, it is a good practise to store relevant data that allow to communicate with the cloud in a separate config file. In this tutorial, that file is called "dl.cfg" and is store in the same location as the current jupyter notebook. The file contains three sections:
- AWS credentials (access key ID and secret access key) needed to programmatically access AWS
- IAM role and IAM policy names
- settings of the Kinesis Firehose delivery stream
- S3 destination bucket name
As a first step, let's extract some of the above mentioned parameters from "dl.cfg" file.

In [1]:
import configparser
import time
import boto3
import json
import random

# Read AWS credentials from the config file
cfg_data = configparser.ConfigParser()
cfg_data.read('dl.cfg')   

# Save AWS credentials
access_key_id     = cfg_data["AWS"]["access_key_id"]
secret_access_key = cfg_data["AWS"]["secret_access_key"]

# Save IAM role and IAM policy settings
RoleName = cfg_data["IAM"]["role_name"]
RoleARN = 'arn:aws:iam::341370630698:role/{}'.format(RoleName)
PolicyName = cfg_data["IAM"]["policy_name"]

account_id = boto3.client(
    'sts',
    aws_access_key_id = access_key_id,
    aws_secret_access_key = secret_access_key).get_caller_identity().get('Account')

# Kinesis Firehose
Region = cfg_data["Firehose"]["region"]
DeliveryStreamName = cfg_data["Firehose"]["stream_name"]
DeliveryStreamType = cfg_data["Firehose"]["delivery_stream_type"]
SizeInMBs = int(cfg_data["Firehose"]["size_in_mb"])
IntervalInSeconds = int(cfg_data["Firehose"]["interval_in_seconds"])
StreamARN = 'arn:aws:firehose:{}:{}:deliverystream/'.format(Region, account_id, DeliveryStreamName)

# S3 Bucket
Bucket = cfg_data['S3']['bucket_name']
BucketARN = 'arn:aws:s3:::{}'.format(Bucket)


The first step consists of creating a S3 bucket that will serve as a destination for the Kinesis Firehose delivery stream. This can be achieved through the following steps:
- Define Boto3 S3 client to programmatically access S3
- Define a function to create a new bucket
- Run the function

In [2]:
# Create S3 client feeding AWS credentials extracted from the config.json file
s3 = boto3.client(
    's3',
    aws_access_key_id=access_key_id,
    aws_secret_access_key=secret_access_key)

# Define a function to create a S3 bucket
def create_bucket(Bucket):
    """
    Create a S3 bucket named 'Bucket'
    """
    
    # Check if a S3 bucket with the same name already exists
    try:
        s3.head_bucket(Bucket=Bucket)
        print('Bucket {} already exists'.format(Bucket))
    except:
        print('Bucket {} does not exist or you have no access'.format(Bucket))
        
        print('Creating bucket {}...'.format(Bucket))

        # Create a new bucket
        response = s3.create_bucket(Bucket=Bucket)
    
        # Loop until the bucket has been created succesfully
        created = False
        while not created:

            for bucket in s3.list_buckets()['Buckets']:
                if bucket['Name'] == Bucket:
                    created = True
                    break
        print('Bucket {} successfully created'.format(Bucket))
        return response
    
# Run the function defined above to create a new S3 bucket
create_bucket(Bucket)
    

Bucket receive-streaming-data already exists


Check if a IAM Role with the same name already exists and delete it if it does. Then create a new IAM Role to enable Kinesis Firehose to write to S3

In order to allow Kinesis Firehose writing data into a S3 bucket, an Identity Access Management (IAM) role should be created. This role will allow AWS services to be called on behalf of the user. Similarly to S3 service, AWS IAM service can be accessed by python SDK Boto3 using a specific client. In the code below, the following operations will be executed:
- define client to control IAM
- check if any role with the name defined in the config file already exists and (if it does) delete it
- create a new role destined to Kinesis Firehose.

In [3]:
# Create IAM client feeding AWS credentials extracted from the config.json file
iam = boto3.client(
    "iam",
    aws_access_key_id = access_key_id,
    aws_secret_access_key = secret_access_key
)

# Try to delete the existing role with the same name, if it exists
try:
    role = iam.get_role(RoleName = RoleName)
    
    print("Role named '{}' already exists".format(RoleName))

    # Extract all the attached policies to the existing role
    attached_policies = iam.list_attached_role_policies(RoleName = RoleName)["AttachedPolicies"]

    # Iterate over all attached policies
    for attached_policy in attached_policies:

        # Extract attached policy ARN
        attached_policy_arn = attached_policy["PolicyArn"]

        # Detach policy from role
        iam.detach_role_policy(
            RoleName = RoleName,
            PolicyArn = attached_policy_arn
        )

    # Delete role
    try:
        delete_role = iam.delete_role(RoleName = RoleName)
        print("Role named '{}' has been deleted".format(RoleName))

    except Exception as e:
        print(str(e))
        
except Exception as e:
    print(str(e))

# Create new IAM role
try:
    role = iam.create_role(
        RoleName = RoleName,
        Description = "Allows Kinesis Firehose Stream to write to S3",
        AssumeRolePolicyDocument = json.dumps(
            {
             "Version": "2012-10-17",
             "Statement": {
               "Effect": "Allow",
               "Principal": {"Service": "firehose.amazonaws.com"},
               "Action": "sts:AssumeRole"
              }
            } 

        )
    )
    print("Role '{}' has been created".format(RoleName))

except Exception as e:
    print(str(e))
 
# Extract role ARN
RoleARN = iam.get_role(RoleName=RoleName)["Role"]["Arn"]
print("Role '{}'s ARN is: '{}'".format(RoleName, RoleARN))


Role named 'KinesisFirehoseWritesToS3' already exists
Role named 'KinesisFirehoseWritesToS3' has been deleted
Role 'KinesisFirehoseWritesToS3' has been created
Role 'KinesisFirehoseWritesToS3's ARN is: 'arn:aws:iam::341370630698:role/KinesisFirehoseWritesToS3'


An IAM role does not grant by default any permission to access specific AWS services. What determines which specific services are accessible is defined by an IAM policy. IAM policies are written in JSON and consist of a list of statements; each statement defines one or more actions, an effect (Allow or Deny), and a resource which the statement is applied to.
In the code below, the following operations will be executed:
- check if a policy with the name defined in the config file already exists
- if a policy already exists, detach the policy from all the role it is attached to
- delete all versions of the policy (including the default version)
- create a new policy allowing Kinesis Firehose specific permissions for the destination S3 bucket
- attach the policy to the role created above.

In [4]:
# Check if policy with the wanted name already exists
try:
    policies = iam.list_policies()["Policies"]
    policy_exists = False
    for policy in policies:
        if policy["PolicyName"] == PolicyName:
            existing_policy_arn = policy["Arn"]
            policy_exists = True
            break          
except:
    print(str(e))

# If a policy with the same name already exists, delete it
if policy_exists:
    print("Policy named '{}' already exists".format(PolicyName))
    
    # Extract all roles
    roles = iam.list_roles()["Roles"]
    
    # Iterate over all the roles
    for role in roles:
        
        # Extract role name
        existing_role_name = role["RoleName"]
        
        # Extract all the attached policy to the role
        attached_policies = iam.list_attached_role_policies(
            RoleName = existing_role_name
        )["AttachedPolicies"]
        
        # Iterate over all the attached policies
        for attached_policy in attached_policies:

            # Extract attached policy ARN
            attached_policy_arn = attached_policy["PolicyArn"]

            # Checking if the policy correspond to the wanted one
            if attached_policy_arn == existing_policy_arn:
                
                # Detach policy from role
                iam.detach_role_policy(
                    RoleName = existing_role_name,
                    PolicyArn = attached_policy_arn
                )
                
                print("Policy with ARN '{}' detached from role '{}'".format(PolicyArn, existing_role_name))
    
    # Extract all the policy versions
    policy_versions = iam.list_policy_versions(
        PolicyArn = existing_policy_arn
    )["Versions"]
    
    # Iterate over all the policy versions
    for policy_version in policy_versions:
        
        # Skip the version if it is a default version
        if policy_version["IsDefaultVersion"]:
            continue
          
        # Extract policy ID
        version_id = policy_version["VersionId"]
        
        # Delete policy version
        iam.delete_policy_version(
            PolicyArn = existing_policy_arn,
            VersionId = version_id
        )
        print("Policy with ARN '{}', version_ID '{}' deleted".format(existing_policy_arn, version_id))
    
    # Delete default version of the policy
    iam.delete_policy(
        PolicyArn = existing_policy_arn
    )
    print("Policy with ARN '{}' deleted".format(existing_policy_arn))
    
else:
    print("Policy named '{}' does not exists".format(PolicyName))
 
PolicyContent = {
                "Version": "2012-10-17",  
                "Statement":
                [    
                    {      
                        "Effect": "Allow",      
                        "Action": [
                            "s3:AbortMultipartUpload",
                            "s3:GetBucketLocation",
                            "s3:GetObject",
                            "s3:ListBucket",
                            "s3:ListBucketMultipartUploads",
                            "s3:PutObject"
                        ],      
                        "Resource": [        
                            "arn:aws:s3:::{}".format(Bucket),
                            "arn:aws:s3:::{}/*".format(Bucket)
                        ]    
                    },        
                    {
                        "Effect": "Allow",
                        "Action": [
                            "kinesis:DescribeStream",
                            "kinesis:GetShardIterator",
                            "kinesis:GetRecords",
                            "kinesis:ListShards"
                        ],
                        "Resource": "arn:aws:kinesis:{}:{}:stream/{}".format(Region, account_id, DeliveryStreamName)
                    },
                ]
            }

# Create policy 
try:
    policy = iam.create_policy(
        PolicyName = PolicyName,
        Description = "Allow to list and access content of the target bucket 'receive-streaming-data'",
        PolicyDocument = json.dumps(PolicyContent)        
    )
    print("Policy named '{}' created".format(PolicyName))
    PolicyArn = policy["Policy"]["Arn"]
    print("Policy named '{}' has ARN '{}'".format(PolicyName, PolicyArn))
except Exception as e:
    print(str(e))

# Attach policy to IAM role
try:
    attachment = iam.attach_role_policy(
        RoleName = RoleName,
        PolicyArn = PolicyArn
    )
    print("Policy named '{}' attached to role '{}'".format(PolicyName, RoleName))
except Exception as e:
    print(str(e))


Policy named 'KinesisWritesToS3receive-streaming-data' already exists
Policy with ARN 'arn:aws:iam::341370630698:policy/KinesisWritesToS3receive-streaming-data' deleted
Policy named 'KinesisWritesToS3receive-streaming-data' created
Policy named 'KinesisWritesToS3receive-streaming-data' has ARN 'arn:aws:iam::341370630698:policy/KinesisWritesToS3receive-streaming-data'
Policy named 'KinesisWritesToS3receive-streaming-data' attached to role 'KinesisFirehoseWritesToS3'


Using the boto3 client for Kinesis Firehose, the following functions are created:
- a delete_stream function whose goal is to identify if a delivery stream with the same name exists and delete it
- a create_stream function whose goal is to create a new delivery stream; for this tutorial, the stream operates with a "Put Records" delivery method and the buffer limits are setup as 5MB/s and 60 seconds a a GZIP compression is used. These parameters can be easily replaced in the "dl.cfg" file.

In [5]:
# Create Kinesis Firehose client feeding AWS credentials extracted from the config.json file
firehose = boto3.client(
    'firehose',
    aws_access_key_id=access_key_id,
    aws_secret_access_key=secret_access_key)

def delete_stream(DeliveryStreamName):
    """
    The function deletes an existing stream named 'DeliveryStreamName'
    """
    
    # Delete the current stream with the same name
    response = firehose.delete_delivery_stream(
        DeliveryStreamName=DeliveryStreamName,
        AllowForceDelete=True
    )

    # Get status of the stream 
    status = firehose.describe_delivery_stream(
    DeliveryStreamName=DeliveryStreamName)[
        'DeliveryStreamDescription']['DeliveryStreamStatus']
    print('{} stream "{}" ...'.format(status, DeliveryStreamName))

    # Wait until the stream is deleted
    i = 0
    while status == 'DELETING':
        time.sleep(10)
        print('Stream "{}" is being deleted, {} seconds elapsed...'.format(DeliveryStreamName, 30*(i+1)))
        try:
            status = firehose.describe_delivery_stream(
                DeliveryStreamName=DeliveryStreamName)['DeliveryStreamDescription']['DeliveryStreamStatus']
            i += 1
        except:
            status = 'DELETED'
    print('Stream "{}" has been succesfully deleted'.format(DeliveryStreamName))

    return status

def create_stream(
    DeliveryStreamName,
    RoleARN,
    BucketARN,
    SizeInMBs=SizeInMBs,
    IntervalInSeconds=IntervalInSeconds,
):
    """
    The function creates a new stream named 'DeliveryStreamName'
    """
         
    # Create a new stream
    response_create = firehose.create_delivery_stream(
        DeliveryStreamName=DeliveryStreamName,
        DeliveryStreamType='DirectPut',
        S3DestinationConfiguration={
            'RoleARN': RoleARN,
            'BucketARN': BucketARN,
            'BufferingHints': {
                'SizeInMBs': SizeInMBs,
                'IntervalInSeconds': IntervalInSeconds
            },
        },
    )
    

    # Get the status of the new stream
    status = firehose.describe_delivery_stream(
        DeliveryStreamName=DeliveryStreamName)['DeliveryStreamDescription']['DeliveryStreamStatus']
    print('{} stream "{}" ...'.format(status, DeliveryStreamName))

    # Wait until the stream is active
    i = 0
    while status == 'CREATING':
        time.sleep(10)
        print('Stream "{}" is being created, {} seconds elapsed...'.format(DeliveryStreamName, 30*(i+1)))
        status = firehose.describe_delivery_stream(
        DeliveryStreamName=DeliveryStreamName)['DeliveryStreamDescription']['DeliveryStreamStatus']
        i += 1

    # Check that the stream is active
    if status == 'ACTIVE':
        print('Stream "{}" has been succesfully created'.format(DeliveryStreamName))
        stream_arn = response_create['DeliveryStreamARN']
        print('Stream "{}" ARN: {}'.format(DeliveryStreamName, stream_arn))
    elif status == 'CREATING_FAILED':
        print('Stream "{}" creation has failed'.format(DeliveryStreamName))

    return status


In the following code the two functions defined above are run in order to create a Kinesis Firehose delivery stream according to the parameters defined in the 'dl.cfg' file

In [10]:
# Check if there is an existing stream with the same name in the same region

try:
    list_stream = firehose.list_delivery_streams()
    
    replace = 'yes'
    
    # Check if the stream already exists
    if DeliveryStreamName in list_stream['DeliveryStreamNames']:

        
        # Ask the user if the stream should be replaced
        replace = input("Stream {} already exists. Do you want to replace it? Type 'yes' to replace, otherwise 'no'".format(DeliveryStreamName))
        print(replace)
        
        # If the user has chosen to replace the stream, delete it and create a new one
        if replace == 'yes':
            
            # Delete stream
            try:
                status = delete_stream(DeliveryStreamName)
            
            except Exception as e:
                print(str(e))
            
            
            # Create new stream
            try:
                status = create_stream(
                    DeliveryStreamName=DeliveryStreamName,
                    RoleARN=RoleARN,
                    BucketARN=BucketARN,
                    SizeInMBs=SizeInMBs,
                    IntervalInSeconds=IntervalInSeconds)
            
            except Exception as e:
                print(str(e))            

        # If the user has chosen not to replace the stream, do nothing
        elif replace == 'no':

            None
            
        else:
            print('input not valid')
            
    # If the stream does not exist, proceed and create a new one
    else:
        
        try:
            status = create_stream(
                DeliveryStreamName=DeliveryStreamName,
                RoleARN=RoleARN,
                BucketARN=BucketARN,
                SizeInMBs=SizeInMBs,
                IntervalInSeconds=int(IntervalInSeconds))

        except Exception as e:
            print(str(e)) 

        
except Exception as e:
    print(str(e))
        

CREATING stream "my_stream" ...
Stream "my_stream" is being created, 30 seconds elapsed...
Stream "my_stream" is being created, 60 seconds elapsed...
Stream "my_stream" is being created, 90 seconds elapsed...
Stream "my_stream" is being created, 120 seconds elapsed...
Stream "my_stream" is being created, 150 seconds elapsed...
Stream "my_stream" is being created, 180 seconds elapsed...
Stream "my_stream" is being created, 210 seconds elapsed...
Stream "my_stream" is being created, 240 seconds elapsed...
Stream "my_stream" is being created, 270 seconds elapsed...
Stream "my_stream" is being created, 300 seconds elapsed...
Stream "my_stream" is being created, 330 seconds elapsed...
Stream "my_stream" is being created, 360 seconds elapsed...
Stream "my_stream" is being created, 390 seconds elapsed...
Stream "my_stream" is being created, 420 seconds elapsed...
Stream "my_stream" is being created, 450 seconds elapsed...
Stream "my_stream" has been succesfully created
Stream "my_stream" ARN:

After the delivery stream has been succesfully created, it can be tested by producing some sample records and streaming them to the delivery stream using the "Put Record" method

In [20]:
# Define a sample record

# Send each record to the delivery stream
for i in range(10000):
    response = firehose.put_record(
        DeliveryStreamName=DeliveryStreamName,
        Record={
            'Data': json.dumps(
                {
                    "sensorId": random.randrange(1,3,1),
                    "currentTemperature": random.randrange(0,35,1),
                    "status": "OK"
                }
            )
        }
    )
    time.sleep(1)
    print(response)
    

{'RecordId': 'qpxbmsDl9aVhVr2SaI0jJdkjunYk/aPz6V9YL4Pl8o3eIXOMyoaC9aTYqis+vTTSkZsNprD31QrsEjfEuCdBpA5zguaIZWctqSNfp/d25YuNVtDu7+7M9GcY1riTOedniDyhCdpa4f0bp21hNv3KenuG6pp8xR/u2Rrey+PzNEp2sUAM6Nem8OL4WCNg7gN+VC70Y2j636QmhORpj+m2iOnWlANTbaKL', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'da7e3aaa-3425-0bdc-81bc-31ef24f3fe61', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'da7e3aaa-3425-0bdc-81bc-31ef24f3fe61', 'x-amz-id-2': 'Hy0N8mvJwdj3DmOcKTa1aOp/2SR1c2W/zcl2BoFii11ZhOLUGuVHz6ybhH0uJfTR9WJH/7Kv/OaCqr7w7WKY0aio1FyYi+kJ', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Thu, 13 Oct 2022 12:48:04 GMT'}, 'RetryAttempts': 0}}
{'RecordId': 'xBgt6dxFlkDr07fHjHxXFSCl2i5s+B4bSLjrGqPBB5vnN1vSTYTyE/pWgBl8K0HQIKdEaDaoL21ikeoj3Gr/Z5Y2f79gIg73v+P857dDH1I3egjc2BsMCTgk2ebpMju40pu1Ja2wgphWWzdNQIEfRtMv6/n2ii4tX6vOB2zFG+44WNPW/D8KLOMj0HMXmDp/+TQNCX1raMIlotiZ+4MXSpxeMtkHWRd6', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'e43ef320-6515-13fc-bff

{'RecordId': 'DFIxY2MRdTT5OdkL7ryEC4hooRh7tW2wKVxKTXoYStBOcxv0742WoBoUQnEv717l07qyB/KQLBaUxZ2mT4xFcYr8cAtIrFfcXYT1T3un6OJEkMJ0cb6rgzIFqMqOTn1fPO6MOMB0Er6hyyUy5Us0GvQpzJD/EkDOdNK1bR7U6fHLLtOJMlOx2MoISOBhjfzElE2bZtgzMtmgRHCczgzbI5WDPYpjihOR', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'e2c17976-08a0-2d6a-b903-72251876d8d7', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'e2c17976-08a0-2d6a-b903-72251876d8d7', 'x-amz-id-2': 'su1cSGOImqiCIVI92xgGkHTeBOaEBSGHI9ZFdNWxvBCl8sDaWxzRq4Ej1AijhQ2xAbGElgE77BzbN17NoXwCKnHeZis2ls2C', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Thu, 13 Oct 2022 12:48:18 GMT'}, 'RetryAttempts': 0}}
{'RecordId': 'ryxeTRH70QLfcpdNze0gUfGIX9pgvLpLksKNyWbjPZQ/Q6xIPN3ED9dIjTNa6roc5vbjcZsAaQ74yl5xaDLbhnHNDZ/KqA1/TevOKJ1icuEih8VO7ZVUl1yfXtHODiXZYMz4ZVTrsWJ7v2pD+8awwezDTHqTrlI6PCYyFEDcoXlN22pzDCGKLVjS59Q6+QwHxv2PBVO5Plh7IcV+SsD20zWul5phPnYT', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'e18fa0dc-1fb6-5aef-ba4

{'RecordId': 'GDzoFd4VIPspnGK0BnCSDjrfE9N+Mm36eCny6B7pDQ0rWho7b0K0mEzshm3NPYAjh2McEZEH3mzmNgQQuk4ttwAeWWra/d9LIsmYZuufZCFh7KtCRxieB7nP7Ht/fWd6kuNefDb9FIIeM5M8rES5v2Jjzv8TPffs4xkHwKx7NiTqMBh/yJwcOb2mmVofmOWa6ntZjUrkNYdkOnlbvbZUDO0O5DoN5Ect', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'fa89668d-ff71-f9b1-a14b-6defefa70c0c', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'fa89668d-ff71-f9b1-a14b-6defefa70c0c', 'x-amz-id-2': 'jKrge7tXoqqhxOHFWK4ucQ1FjZ/WBFgyUFHNtKZhtIa1SpSHbH3SsklNa26eM/eF00G+tKVB5Nxia2UQ1jvSGNlXrnD/zcxL', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Thu, 13 Oct 2022 12:48:33 GMT'}, 'RetryAttempts': 0}}
{'RecordId': 'eMy3Qw5XXLhL8Wp7jFnXBoU2ywJpUovEBTAeGTEA8kl//Pefrb5BmW7NxpAjW2s53ltyVyH7XoWOGlzSkZvfW3LELJqHVkqWkx5kGQdZShd6XyzRZKi/u9T764XASI1Rjye2sFIMKBRNINJOIXeMrr8uRcURJI6EaCO5YvgUCHJUlcVChTxA+/Vzn+f22on2RNVjhvRI4ownDyX78TAfGfwkjFnQJVXv', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'c55e8247-2922-ab00-9e9

{'RecordId': 'u6C0ODy6DKbg/GV9LC+4gOeTwMdTT0eYjUmuvFF3zcdtoBz+uhqvnBykegNeUfyNIUUyMn/ZZ8IMLX5omr9BdUgDJ/zlB4CUtE2462xkXvxYHWh4xrXQeYtK80RQ1uRf6AZ1KlPb6dL7nFO+7Dx3sONfasukfeSIzyZumxw/B2d8bPVWDom/skyvsJZoLr9I8sbJp2T3b5xUkbLXi92EWj1tSGjDTpzh', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'e85c38de-26ae-479e-b39e-33ae3678b223', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'e85c38de-26ae-479e-b39e-33ae3678b223', 'x-amz-id-2': 'kLb1/PlvDO8HB+/GHKC8P0rxQ52LjAs03+ovCib9BUD9WCIt2MfZUQcfQDdVL+FVV/JqgyQiqSSH9ooBd5Ak+N0zK37r3nsO', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Thu, 13 Oct 2022 12:48:48 GMT'}, 'RetryAttempts': 0}}
{'RecordId': 'woqvGeqs6nXel1y+Q/SLZqBNWkevwHl3LqpBjbiRpX+ShbMTlawjqL6oAb6C450EW0LibZW5J27gd2/NLHBo+pdIxH5wTOqODNK8IofSqnYJ5kQyvcUUaUakJlLi5dgdKRzVVkTqXlqZsRe5iDV+4MBkBBxTdr1/ZbvR7sjrM2SKbVCUMoJ6N/qWmMt32mVM6K4zjVFYKZi5tuV0gK/EUDdlVfOmY3Fq', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'df2efd86-cf8c-3c05-84e

{'RecordId': 'yP2knqI4r52hRqrM7bESYYtkqYCidDyFS4ZuH58nipSfpph78n091J/onw8LoE8fhMPIDVpUeuEVtLAdMpdhM2m7KLg/evgz0mS3W6AyJEggl+lFVH82CudbUtcYn6AF5vc8TyiAGubdWug0B8Ctfl7kduPTfNXouJDWhIqq5KIWnN6oV28a4A9oj4GneBTyRPPjmElHGRNnP1ryP/ba7HpsojB5zXhE', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'fd93522a-4128-73eb-a651-595551fe8656', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'fd93522a-4128-73eb-a651-595551fe8656', 'x-amz-id-2': 'TTvhMMKWBjJ8w/S4SFWjPcwNlG+qcnxbyy8WMOMio6GhGlyrTGXUv3Mk9mW4r/yeNqrt6uI6p1JHWDRdnKd4nb6uU1Tdy07B', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Thu, 13 Oct 2022 12:49:02 GMT'}, 'RetryAttempts': 0}}
{'RecordId': '75ex+cTyNUypTofKVdvkh6450Tgg8HptVhGSnNPPIcT58ft2b/RMelB1NBo+5Ai3cPoKb11oZrFbUvOkc+T+3q33vwZ+kREhiXR3kE05zkcXtTS+HqRYD/Qdo+VF37sL0VfDvEm7UoqX8wr6WeLbabQSphVAGYjpaLg6gfy7kltFG/NCY8zsnDNfp664QqfHagp1a20ZwDSaWk61Zmtu1+6HNBr6pcUN', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'd98e5cdc-623d-eb03-824

...

{'RecordId': 'KYyQdX3Dap898/aoa6H9rL28euVecNrn4IXhhaaAl/EcUmrtFQGC/Jo6Ayn0Io4GTK+iVObWYv6oLtbPtaP7pITCvtezcPPVKr12MskzF3m/3IqBIbiL+4BY3LRpWHKJnRzcgbv6EYeuXs2+uUaoNepRPSMKe6JJUfI/m2X1OZmkfsff92NldBP4PkxLsj3iJ+jy5eR9sVZMusznVX7GomegJgrwCVyt', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'c2afa97f-f6c3-34e8-996c-bee82a9694c6', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'c2afa97f-f6c3-34e8-996c-bee82a9694c6', 'x-amz-id-2': 'ODA82aWWSy3rySklb/5NQgbYfiZqvLGKxNEIGUYcRUb/vupkl6TpQvwuxa58YdxodhYEJQvJPI2bYb9Ry9Fshk+oPsd8TkeM', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Fri, 14 Oct 2022 07:52:54 GMT'}, 'RetryAttempts': 0}}
{'RecordId': 'vQeYzYiJzUukOSF7Z/EzCyA7M7b5+9bMcTqiD/0Hd4mKkk/jDLST1fo3nr8YDSW4ntvZtqw+aFg5pz0gnmgX6+z586jB35hkff9elBmWYNkho0nTOn0bOGxYV6+hnPAaFwJSnhL0W9ec7zmS/Hib5u32KwFD7XXIFnHJP7y0Y8qXqf0rnrSOUW146dTwdeVP4lbxZvXQ+XHWvbIZCdDaNpxp2FC7vbgO', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'e81234dc-002d-4d12-b3d

{'RecordId': '374k8im2KOb8MnRJusQUb8bJ16IP7NpSLi+LVejRo9m1vPR5D44wZ3Tx9OXk4jBxRHKXKe0BNUjejQZllcU6ijze3VJA1DU8DC/ZtdjfHqkB1Seed/DZbB872v17a/2jaO2xtV5d4TAlT20V0tKvZoG6ES6uPwvDbRBfslpfCRJwGGRM3NRfAHKoC7m9vpJVTepub0BfJu2ErToy32lJ8JgDyzLA1qFu', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'eaab18d1-50f3-690e-b168-0f748ca6c920', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'eaab18d1-50f3-690e-b168-0f748ca6c920', 'x-amz-id-2': '0VBfk72HEC/oCYeZu9sbrj71nIa1iziEjJdjCp296DewawmrIXJExdxGPzGHjY/MTzrmcGJMCzZcLuJnwFpHNC2VuoW7NMFH', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Fri, 14 Oct 2022 07:53:08 GMT'}, 'RetryAttempts': 0}}
{'RecordId': '8unrJdAr/oQuPTuGuxqEuSMEy8opLHFxNuCvyqm56AUBxPpMXrxuB7hQG7wBZU/5Mk8HAHkBzvtuZ8BanchhlKN4n8KxzHlf92Tpujtbh/QKNxSsxqKw92irvEtK7rQLuTofbaZsKjTUHW2X/YkVQRKHy3pp0GZ8q9yOzM7Jb47RfgwP2nQ1WMlRNV0hW4h9vChuNigFO/twTsJNUvdOIcj5A0G1AYyT', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'ea0a3a44-6581-7b6a-b1c

{'RecordId': 'vrMTlUkHkN/lUTeGeOHn/Ujsb3G9niayZ+irtlEv5VIk3MBflvnNdiHHxJbade+kQddeu0IBBR0dOeD1qDzQsEoyX/UmMOSHKbnEUXDlsqge/TYEg1sS9ngrajHS0qWf1LcRcstV6uyiY6hup9Z19Jn8RLXzCoZQvNC6SQojDN2jhK13WK3XHIr60cWgQ2yD16oGZMeRSfPzxI21beH+AEtecCNTnXSz', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'e6aa6fcc-da48-789c-bd69-7878061dd8b2', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'e6aa6fcc-da48-789c-bd69-7878061dd8b2', 'x-amz-id-2': 'KT4IqsYJpDbYBGPNZ3WVjGtMfDbX85wvJNLJxPPWMsypL2htvxELKZbzFXjmMQ4pRWX1vYEWtMSjIOBeT30hCE7LaZumC7po', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Fri, 14 Oct 2022 07:53:23 GMT'}, 'RetryAttempts': 0}}
{'RecordId': 'FtNjtSs+IhUEzZzcKmkYJ9TOI6pfquM5+qCg9S8Asahmooj2m2luFyj5lUWFctF+kRmWLmmR5xKwhst0BgvpKvx02o1o7zbWRXcNG4lfeAqlY421OxH1e4IEOHkICfUKDZIt51Jkv45uI5AF8L7cBUVWpPRyKwNo3Jy/bL6afQbh/vC+dS2PMPhPO2S+ldLkA/mGHsSGdXwxNSOgt/m5nVqSxOFvX4dF', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'db6069c1-878d-dcbb-80a

{'RecordId': 'CWWAjT4S/EaUG1FWI/BYueK1lpNtQb7+ohHhFIgIKXH7F2lnFT1rOtq9/J/GfNjeCt+3KsJs8+zgEpVwWxHo8cqV0YrUn88g3nr0VeW8qIhinFlHlxdQjsGaAzj2tFDabtr3E0MX3vyUpwwbu5awFqMJ7QkVxSHW1+Rg3m2+y490+S1n9lIwEDRjnep+Vl+IP7msrLF7lMalpWj8DdeY8YWDrGn7Yv09', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'e8d6415a-083f-5252-b315-569894accbda', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'e8d6415a-083f-5252-b315-569894accbda', 'x-amz-id-2': 'AmTvQyFZ3kUU+KMSuPopH8hzwDW8xCdjkwcnmLr/UUBh4kodD8nXzpXtbew384QGYNDczzePo+vWFgDMcICqXputYPlD6XtQ', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Fri, 14 Oct 2022 07:53:37 GMT'}, 'RetryAttempts': 0}}
{'RecordId': 'oUcHU5XNtCfcVIvB0q1N93VoISqx1tcNF2mI0T98vTbwZWJw7zqX/DFSWQANaCemyIP/yhepooVK7ZcMSQWVTcLmXJ3pOGIhfdJCZIvzFsHA0NN+RLkpJz7f1SHzBM6UxPzaJGO3JSjEX0HFM0BxkpgCIBDfzi0z9Z47wXE2wGInd+SiYTQr++JU1mzSff2XRBsbEiOJjS0IY0GWDRgXTEbq/fytVPYA', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'd3c2a9fd-d5f1-fac8-880

{'RecordId': 'XPugbPMHwK2P1LZ5V/jckVf0msMTIdQduwLgbrz7cs/2BFPCt38Al8GZ97iV4VrGhhGJingCqTafCZ7G0W/bQkXSLbtpF2D1U2ZBqtMZ8Xf3FXeZs0B0JLNwMX2JCqJfmSroAVcRt3L+aYheB//EewDSIv8S6EaFDLMpII7Oxh5XtsD1SoKVqx44RzmSNiAtLlIICdDZ+uM1T43rAWl3yqyJ9Vxq84J7', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'cde4ab89-b9c5-0bb4-9627-bc592556923c', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amzn-requestid': 'cde4ab89-b9c5-0bb4-9627-bc592556923c', 'x-amz-id-2': 'Vi66EwArJw38nFtSAbm1/hM7uA7r8BuEfeMdvBl71HVkyafdqLdyEOExJEBTQeGlTYPIuIWMKw7kMjjIng5tovEvZOfnB01u', 'content-type': 'application/x-amz-json-1.1', 'content-length': '257', 'date': 'Fri, 14 Oct 2022 07:53:52 GMT'}, 'RetryAttempts': 0}}
{'RecordId': 'aRrrfaLQO4/tdp6XPjGT6rQLfpWxpDIBP8/K67S4g2A1YkT9Ib+Z9OJ3/aCtCpv+ynmQ6abmtoXSjWA3/ltYkUbogRm2ELeW0MVJLQrZNgcOA2pF5GQRCR+ggIiGdtv8q9pKyG5ix6RUQHDym498FLcpr6YGmPijFhZ09NBfdz8NsqKgir3+V77JdCAc4tqClbM7Mxo44HggeJQ8IvERKxKRekT5f3CJ', 'Encrypted': False, 'ResponseMetadata': {'RequestId': 'c3d1f879-c59b-ee17-981

Finally, the delivery stream can be deleted to avoid extra cost.

In [9]:
# Delete stream

# Ask the user if the stream should be deleted
delete = input("Do you want to delete Stream {}? Type 'yes' to delete, otherwise 'no'".format(DeliveryStreamName))

# If the user has chosen to replace the stream, delete it and create a new one
if delete == 'yes':

    # Delete stream
    try:
        status = delete_stream(DeliveryStreamName)

    except Exception as e:
        print(str(e))

Do you want to delete Stream my_stream? Type 'yes' to delete, otherwise 'no'yes
An error occurred (ResourceNotFoundException) when calling the DeleteDeliveryStream operation: Firehose my_stream under account 341370630698 not found.
